In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pickle, copy, warnings
warnings.filterwarnings("ignore")

In [2]:
data = pickle.load(open('data/inverse/cust_id.pkl', 'rb'))

In [3]:
for k1, v1 in data.items():
    for k2, v2 in v1.items():
        acc_amt = 0
        for s in v2["data"]:
            if s["source"] == 2:
                s["amt"] = s["tx_amt"] * s["exchg_rate"]
                if s["debit_credit"] == "DB":
                    acc_amt += s["amt"]
                else:
                    acc_amt -= s["amt"]
                s["acc_amt"] = acc_amt

In [4]:
# 抓出info資料sar為1的樣本所涵蓋的區間資料
sar_1 = {}
for k1, v1 in data.items():
    for k2, v2 in v1.items():
        if (v2["data_type"] == "train"):
            if (v2["sar"] == 1):
                sar_1[k1] = v2

In [7]:
a = 0
for k1, v1 in data.items():# id_
    for k2, v2 in v1.items(): # id_的info sample
        flag = 0
        if (v2["data_type"] == "train"):
            if (v2["sar"] == 1):
                for s in v2["data"]: # info sample涵蓋區間的所有資料
                    if (s["source"] == 1): # dp 資料
                        flag = 1 if s["amt"] > 100 else 0
        a += flag
a

84

In [5]:
sar_1

{40: {'sar': 1.0,
  'data_type': 'train',
  'data': array([{'cust_id': 40, 'date': Timestamp('2021-06-12 00:00:00'), 'country': 130, 'cur_type': 47, 'amt': 109301.0, 'source': 1},
         {'cust_id': 40, 'date': Timestamp('2021-06-12 00:00:00'), 'country': 130, 'cur_type': 47, 'amt': 78072.0, 'source': 1},
         {'cust_id': 40, 'date': Timestamp('2021-06-14 00:00:00'), 'country': 130, 'cur_type': 47, 'amt': 146.0, 'source': 1},
         {'cust_id': 40, 'date': Timestamp('2021-06-16 00:00:00'), 'country': 130, 'cur_type': 47, 'amt': 146.0, 'source': 1},
         {'cust_id': 40, 'date': Timestamp('2021-06-18 00:00:00'), 'country': 130, 'cur_type': 47, 'amt': 193.0, 'source': 1},
         {'cust_id': 40, 'date': Timestamp('2021-06-18 00:00:00'), 'country': 130, 'cur_type': 47, 'amt': 31230.0, 'source': 1},
         {'cust_id': 40, 'date': Timestamp('2021-06-18 00:00:00'), 'country': 130, 'cur_type': 47, 'amt': 27294.0, 'source': 1},
         {'cust_id': 40, 'date': Timestamp('2021-06-

In [ ]:
a = 0
b = 0
c = 0
d = 0
for k1, v1 in data.items():
    for k2, v2 in v1.items():
        flag_a = 0
        flag_b = 0
        for s in v2["data"]:
            if (s["source"] == 2) & (v2["data_type"] == "train"):
                if v2["sar"] == 1:
                    if (s["cross_bank"] == 0) & (s["ATM"] == 1):
                        flag_a = 1
                    else:
                        flag_b = 1
        if (v2["data_type"] == "train"):
            a += flag_a
            b += flag_b
            c += v2["sar"]
            d += 1
a, b, c, d

In [ ]:
a = 0
b = 0
test = []
for k1, v1 in data.items():
    for k2, v2 in v1.items():
        flag_a = 0
        if (v2["data_type"] == "test"):
            for s in v2["data"]:
                if (s["source"] == 2):
                    if (s["cross_bank"] == 0) & (s["ATM"] == 1):
                        flag_a = 1

        v2["data"][-1]["sar_flag"] = flag_a
        test.append(v2["data"][-1])
        a += flag_a
        b += 1
a, b

In [ ]:
test = pd.DataFrame(test)
test = test.iloc[:, :3]
test["sar_flag"].value_counts()

In [ ]:
test_idx = test.query("sar_flag == 1")["alert_key"]
test_idx

In [ ]:
submit = pd.read_csv("data/submit/1114.csv")
submit = submit.set_index("alert_key")
submit.loc[test_idx] = 1
submit = submit.reset_index()
submit = submit.sort_values("probability", ascending = False)
submit.to_csv("data/submit/1115.csv", index = False)

In [ ]:
# 分開各來源的資料
train_g = {0: [], 1: [], 2: [], 3: [], 4: []}
test_g = {0: [], 1: [], 2: [], 3: [], 4: []}

for k1, v1 in data.items():
    for k2, v2 in v1.items():
        if v2["data_type"] == "train":
            sar = v2["sar"]
            for v3 in v2["data"]:
                train_g[v3["source"]].extend([v3])
        else:
            for v3 in v2["data"]:
                test_g[v3["source"]].extend([v3])

In [ ]:
for k, v in train_g.items():
    train_g[k] = pd.DataFrame(v)

for k, v in test_g.items():
    test_g[k] = pd.DataFrame(v)